# install VLLM

There is a prior version of the SDK that was upstreamed into the main vLLM repository.  However, most of the time we want to install from source from the aws-neuron fork.  

Instructions are available here:  https://awsdocs-neuron.readthedocs-hosted.com/en/latest/libraries/nxd-inference/developer_guides/vllm-user-guide.html#nxdi-vllm-user-guide

However, the steps are below.  Run the next three cells.  The pip installs could take 5 minutes.

The AWS workshop environment deploys using a Neuron DLAMI with a recent SDK.  If you are deploying this in your own environment, you may need to match the branch to your SDK version or follow the latest instructions at the link above.

In [1]:
%%bash
git clone -b 2.25.0 https://github.com/aws-neuron/upstreaming-to-vllm.git


Cloning into 'upstreaming-to-vllm'...
Note: switching to '1646d106d1bce4c3f4f3e97aa4567ff3b65902ba'.

You are in 'detached HEAD' state. You can look around, make experimental
changes and commit them, and you can discard any commits you make in this
state without impacting any branches by switching back to a branch.

If you want to create a new branch to retain commits you create, you may
do so (now or later) by using -c with the switch command. Example:

  git switch -c <new-branch-name>

Or undo this operation with:

  git switch -

Turn off this advice by setting config variable advice.detachedHead to false



In [2]:
%pip install --quiet -r /home/ubuntu/environment/upstreaming-to-vllm/requirements/neuron.txt
#expected to produce no output for 4 or 5 minutes.  Remove the --quiet flag if you want to see ALL the packages installed!  Or look in the neuron.txt requirements doc.

Note: you may need to restart the kernel to use updated packages.


In [3]:
!VLLM_TARGET_DEVICE="neuron" pip install --quiet -e /home/ubuntu/environment/upstreaming-to-vllm/.
# expected to product no output for 5 or 6 minutes

# Download copies of the model to deploy
We are downloading a copy of the stock Qwen3-8B model as well as the compiled version from Hugging Face.


In [1]:
!hf download aws-neuron/Qwen3-8BSharded --local-dir /home/ubuntu/environment/qwen3
#this could take 2-3 minutes

Fetching 92 files:   0%|                                 | 0/92 [00:00<?, ?it/s]Downloading 'context_encoding_model/_tp0_bk0/metaneff.pb' to '/home/ubuntu/environment/qwen3/.cache/huggingface/download/context_encoding_model/_tp0_bk0/BCY-7ytH60-7foU2jPAwyXM0h6A=.0aef68f833b52be82fd0e17410bcfd279e5719338cb746c0619d5139fc4a3d02.incomplete'

metaneff.pb:   0%|                                  | 0.00/1.04M [00:00<?, ?B/s]

graph.neff:   0%|                                   | 0.00/1.56M [00:00<?, ?B/s]Downloading 'README.md' to '/home/ubuntu/environment/qwen3/.cache/huggingface/download/Xn7B-BWUGOee2Y6hCZtEhtFu4BE=.b927557cb56ad1a3e3471652013f4035328be15b.incomplete'
metaneff.pb: 100%|█████████████████████████| 1.04M/1.04M [00:00<00:00, 36.3MB/s]
Download complete. Moving file to /home/ubuntu/environment/qwen3/context_encoding_model/_tp0_bk0/metaneff.pb
graph.neff: 100%|██████████████████████████| 1.56M/1.56M [00:00<00:00, 49.4MB/s]
Download complete. Moving file to /home/ubuntu/environment

In [2]:
!hf download Qwen/Qwen3-8B --local-dir /home/ubuntu/environment/Qwen3-8B
#This is the stock model.  It could take 3-4 minutes

Fetching 15 files:   0%|                                 | 0/15 [00:00<?, ?it/s]Downloading 'model-00002-of-00005.safetensors' to '/home/ubuntu/environment/Qwen3-8B/.cache/huggingface/download/ewHVStNi_qTCwOvZyUK4XvcG7h0=.5991236cea6fe21f3d43cab0f0e84448734fbbe0789816202989f2ddc9d18282.incomplete'



generation_config.json: 100%|██████████████████| 239/239 [00:00<00:00, 1.34MB/s]
Download complete. Moving file to /home/ubuntu/environment/Qwen3-8B/generation_config.json

LICENSE: 11.3kB [00:00, 55.7MB/s]
Download complete. Moving file to /home/ubuntu/environment/Qwen3-8B/LICENSE

merges.txt: 0.00B [00:00, ?B/s]

README.md: 0.00B [00:00, ?B/s]


README.md: 16.7kB [00:00, 20.3MB/s]                   | 0.00/728 [00:00<?, ?B/s]
Download complete. Moving file to /home/ubuntu/environment/Qwen3-8B/README.md
config.json: 100%|█████████████████████████████| 728/728 [00:00<00:00, 1.59MB/s]
Download complete. Moving file to /home/ubuntu/environment/Qwen3-8B/config.json
merges.txt: 1.67MB [00:00, 58.5MB/s]
Download complete. Moving file to /home/ubuntu/environment/Qwen3-8B/merges.txt

model-00002-of-00005.safetensors:   0%|             | 0.00/3.99G [00:00<?, ?B/s]Downloading 'model-00003-of-00005.safetensors' to '/home/ubuntu/environment/Qwen3-8B/.cache/huggingface/download/W6LiZUqSlTR2RfaiI-P

# Make sure you restart your kernel
If you get an error that vllm could not be found, it is because you didn't restart your kernel after installing it above

May take 8 minutes to run

# Offline infereence example

In this example, we load the qwen3 precompiled model artifacts (or NEFF files) and the model presharded for two cores.  We do this because of the system memory limitations of the trn1.2xlarge (32GB of system RAM).  The trn1.2xlarge also has 32GB of device RAM on the Trainium1 device (that has two Neuron cores), but system RAM is (usually) our limiter for compiling.

In [3]:
import os
from vllm import LLM, SamplingParams
os.environ['VLLM_NEURON_FRAMEWORK'] = "neuronx-distributed-inference"
os.environ['NEURON_COMPILED_ARTIFACTS'] = "/home/ubuntu/environment/qwen3"
#os.environ['BASE_COMPILE_WORK_DIR'] = "/home/ubuntu/qwen3/"
llm = LLM(
    model="/home/ubuntu/environment/Qwen3-8B", #model weights
    max_num_seqs=1,
    max_model_len=1024,
    device="neuron",
    tensor_parallel_size=2,
    override_neuron_config={})
prompts = [
    "Hello, my name is",
    "The president of the United States is",
    "The capital of France is",
    "The future of AI is",
]
# note that top_k must be set to lower than the global_top_k defined in
# the neuronx_distributed_inference.models.config.OnDeviceSamplingConfig
sampling_params = SamplingParams(top_k=10, temperature=0.8, top_p=0.95)
outputs = llm.generate(prompts, sampling_params)
for output in outputs:
    prompt = output.prompt
    generated_text = output.outputs[0].text
    print(f"Prompt: {prompt!r}, Generated text: {generated_text!r}")

# Free up the Neuron Cores for the next step -- in production, keep the object around to avoid load times and warmup times
del llm

/home/ubuntu/environment/upstreaming-to-vllm/vllm/__init__.py:5: RuntimeWarning: Failed to read commit hash:
No module named 'vllm._version'
  from .version import __version__, __version_tuple__  # isort:skip


WARNING 08-11 19:43:14 [__init__.py:25] The vLLM package was not found, so its version could not be inspected. This may cause platform detection to fail.
INFO 08-11 19:43:14 [__init__.py:243] Automatically detected platform neuron.
WARNING 08-11 19:43:18 [_custom_ops.py:21] Failed to import from vllm._C with ModuleNotFoundError("No module named 'vllm._C'")
INFO 08-11 19:43:21 [__init__.py:31] Available plugins for group vllm.general_plugins:
INFO 08-11 19:43:21 [__init__.py:33] - lora_filesystem_resolver -> vllm.plugins.lora_resolvers.filesystem_resolver:register_filesystem_resolver
INFO 08-11 19:43:21 [__init__.py:36] All plugins in this group will be loaded. Set `VLLM_PLUGINS` to control which plugins to load.
INFO 08-11 19:43:44 [config.py:821] This model supports multiple tasks: {'embed', 'generate', 'classify', 'reward', 'score'}. Defaulting to 'generate'.
WARNING 08-11 19:43:44 [arg_utils.py:1611] device type=neuron is not supported by the V1 Engine. Falling back to V0. 
INFO 08-

/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed/parallel_layers/layers.py:14: DeprecationWarning: torch_neuronx.nki_jit is deprecated, use nki.jit instead.
  from .mappings import (
/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed/parallel_layers/layers.py:14: DeprecationWarning: torch_neuronx.nki_jit is deprecated, use nki.jit instead.
  from .mappings import (
/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed/parallel_layers/layers.py:14: DeprecationWarning: torch_neuronx.nki_jit is deprecated, use nki.jit instead.
  from .mappings import (
/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed/modules/moe/blockwise.py:42: DeprecationWarning: torch_neuronx.nki_jit is deprecated, use nki.jit instead.
  component, error = import_nki(config)
/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed/modules/moe/blockwise

WARNING 08-11 19:45:26 [neuron.py:68] Pin memory is not supported on Neuron.
WARNING 08-11 19:45:26 [neuron_model_runner.py:151] On-device sampling is turned on in Neuron by default, only top_k, top_p, and temperature are current supported sampling parameters. To turn off the on-device sampling, please set the environment variable NEURON_ON_DEVICE_SAMPLING_DISABLED=1.
INFO 08-11 19:45:26 [parallel_state.py:1064] rank 0 in world size 1 is assigned as DP rank 0, PP rank 0, TP rank 0, EP rank 0


/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed_inference/modules/attention/utils.py:14: DeprecationWarning: torch_neuronx.nki_jit is deprecated, use nki.jit instead.
  from neuronx_distributed_inference.modules.custom_calls import neuron_cumsum
/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed_inference/modules/lora_serving/lora_model.py:12: DeprecationWarning: torch_neuronx.nki_jit is deprecated, use nki.jit instead.
  from neuronx_distributed_inference.modules.attention.gqa import GQA, GroupQueryAttention_QKV
/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed_inference/modules/lora_serving/lora_model.py:12: DeprecationWarning: torch_neuronx.nki_jit is deprecated, use nki.jit instead.
  from neuronx_distributed_inference.modules.attention.gqa import GQA, GroupQueryAttention_QKV
/opt/aws_neuronx_venv_pytorch_latest/lib/python3.10/site-packages/neuronx_distributed_inference/modu

...

INFO:Neuron:Warmup completed in 1.1553475856781006 seconds.


INFO 08-11 19:49:36 [neuronx_distributed.py:244] Successfully loaded precompiled model artifacts from /home/ubuntu/environment/qwen3
INFO 08-11 19:49:36 [executor_base.py:112] # neuron blocks: 1, # CPU blocks: 0
INFO 08-11 19:49:36 [executor_base.py:117] Maximum concurrency for 1024 tokens per request: 1.00x
INFO 08-11 19:49:36 [llm_engine.py:434] init engine (profile, create kv cache, warmup model) took 0.00 seconds


Adding requests:   0%|          | 0/4 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/4 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Prompt: 'Hello, my name is', Generated text: " Alex, and I am a 17-year-old who's been struggling with"
Prompt: 'The president of the United States is', Generated text: ' currently the most powerful person in the world, but the president of the United States'
Prompt: 'The capital of France is', Generated text: ' located in the north of the country. Is this statement true or false? The'
Prompt: 'The future of AI is', Generated text: ' a multifaceted tapestry woven from threads of opportunity, risk, and the'


# Online inference example.
In this case, we are loading the model directly from Hugging Face and compiling what we need as we go (this is a 1.1B parameter model, so it needs less system RAM to compile than the Qwen3-8B example above)
It may take 5 minutes for the model to download, compile and run.

Because you are running this in a Jupyter notebook, this cell will keep running until you stop it.  The server should remain available (and using the Neuron cores) until you stop it.  

You'll run this cell with different parameters your instructor will be discussing and using the guidellm tool in the Benchmark.ipynb notebook to run against this server.

Run the next cell and wait until you see something like this (it should take about 5 minutes):
```
INFO:     Started server process [21298]
INFO:     Waiting for application startup.
INFO:     Application startup complete.
```

In [5]:
!VLLM_NEURON_FRAMEWORK='neuronx-distributed-inference' python -m vllm.entrypoints.openai.api_server \
    --model="TinyLlama/TinyLlama-1.1B-Chat-v1.0" \
    --max-num-seqs=128 \
    --max-model-len=1024 \
    --tensor-parallel-size=2 \
    --port=8080 \
    --device "neuron" 

/home/ubuntu/environment/upstreaming-to-vllm/vllm/__init__.py:5: RuntimeWarning: Failed to read commit hash:
No module named 'vllm._version'
  from .version import __version__, __version_tuple__  # isort:skip


WARNING 08-12 01:01:45 [__init__.py:25] The vLLM package was not found, so its version could not be inspected. This may cause platform detection to fail.
INFO 08-12 01:01:45 [__init__.py:243] Automatically detected platform neuron.
WARNING 08-12 01:01:46 [_custom_ops.py:21] Failed to import from vllm._C with ModuleNotFoundError("No module named 'vllm._C'")
INFO 08-12 01:01:47 [__init__.py:31] Available plugins for group vllm.general_plugins:
INFO 08-12 01:01:47 [__init__.py:33] - lora_filesystem_resolver -> vllm.plugins.lora_resolvers.filesystem_resolver:register_filesystem_resolver
INFO 08-12 01:01:47 [__init__.py:36] All plugins in this group will be loaded. Set `VLLM_PLUGINS` to control which plugins to load.
INFO 08-12 01:01:48 [config.py:1957] Disabled the custom all-reduce kernel because it is not supported on current platform.
WARNING 08-12 01:01:48 [utils.py:1414] argument 'device' is deprecated
INFO 08-12 01:01:48 [api_server.py:1288] vLLM API server version 0.9.0.dev
INFO 08-